In [ ]:
#60
#問題の指定ページからダウンロードするとエラーが発生するので、https://ja.stackoverflow.com/questions/78347/not-a-gzipped-file-b%E3%81%AE%E3%82%A8%E3%83%A9%E3%83%BC を参考にダウンロードする

!wget https://s3.amazonaws.com/dl4j-distribution/GoogleNews-vectors-negative300.bin.gz

--2021-11-07 08:26:20--  https://s3.amazonaws.com/dl4j-distribution/GoogleNews-vectors-negative300.bin.gz
Resolving s3.amazonaws.com (s3.amazonaws.com)... 52.217.9.78
Connecting to s3.amazonaws.com (s3.amazonaws.com)|52.217.9.78|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1647046227 (1.5G) [application/x-gzip]
Saving to: ‘GoogleNews-vectors-negative300.bin.gz’

GoogleNews-vectors- 100%[===================>]   1.53G  34.1MB/s    in 48s     

2021-11-07 08:27:09 (32.6 MB/s) - ‘GoogleNews-vectors-negative300.bin.gz’ saved [1647046227/1647046227]



In [ ]:
from gensim.models import KeyedVectors

model = KeyedVectors.load_word2vec_format('./GoogleNews-vectors-negative300.bin.gz', binary=True)

In [ ]:
#確認
model['United_States']

array([-3.61328125e-02, -4.83398438e-02,  2.35351562e-01,  1.74804688e-01,
       -1.46484375e-01, -7.42187500e-02, -1.01562500e-01, -7.71484375e-02,
        1.09375000e-01, -5.71289062e-02, -1.48437500e-01, -6.00585938e-02,
        1.74804688e-01, -7.71484375e-02,  2.58789062e-02, -7.66601562e-02,
       -3.80859375e-02,  1.35742188e-01,  3.75976562e-02, -4.19921875e-02,
       -3.56445312e-02,  5.34667969e-02,  3.68118286e-04, -1.66992188e-01,
       -1.17187500e-01,  1.41601562e-01, -1.69921875e-01, -6.49414062e-02,
       -1.66992188e-01,  1.00585938e-01,  1.15722656e-01, -2.18750000e-01,
       -9.86328125e-02, -2.56347656e-02,  1.23046875e-01, -3.54003906e-02,
       -1.58203125e-01, -1.60156250e-01,  2.94189453e-02,  8.15429688e-02,
        6.88476562e-02,  1.87500000e-01,  6.49414062e-02,  1.15234375e-01,
       -2.27050781e-02,  3.32031250e-01, -3.27148438e-02,  1.77734375e-01,
       -2.08007812e-01,  4.54101562e-02, -1.23901367e-02,  1.19628906e-01,
        7.44628906e-03, -

In [ ]:
#61
model.similarity('United_States', 'U.S.')

0.73107743

In [ ]:
#62
import numpy as np
import pandas as pd

simularities = model.most_similar("United_States")
pd.DataFrame(
    simularities,
    columns = ['単語', '類似度'],
    index = np.arange(len(simularities)) + 1
)

単語       類似度
1      Unites_States  0.787725
2      Untied_States  0.754137
3       United_Sates  0.740072
4               U.S.  0.731077
5   theUnited_States  0.640439
6            America  0.617841
7       UnitedStates  0.616731
8             Europe  0.613299
9          countries  0.604480
10            Canada  0.601907

In [ ]:
#63
simularities = model.most_similar(positive=['Spain', 'Athens'], negative=['Madrid'])

pd.DataFrame(
    simularities,
    columns = ['単語', '類似度'],
    index = np.arange(len(simularities)) + 1
)

単語       類似度
1                   Greece  0.689848
2   Aristeidis_Grigoriadis  0.560685
3       Ioannis_Drymonakos  0.555291
4                   Greeks  0.545069
5         Ioannis_Christou  0.540086
6        Hrysopiyi_Devetzi  0.524844
7                 Heraklio  0.520776
8            Athens_Greece  0.516881
9                Lithuania  0.516687
10                Iraklion  0.514679

In [ ]:
#64(準備)
!wget http://download.tensorflow.org/data/questions-words.txt

--2021-11-07 08:29:40--  http://download.tensorflow.org/data/questions-words.txt
Resolving download.tensorflow.org (download.tensorflow.org)... 108.177.96.128, 2a00:1450:4013:c06::80
Connecting to download.tensorflow.org (download.tensorflow.org)|108.177.96.128|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 603955 (590K) [text/plain]
Saving to: ‘questions-words.txt’

questions-words.txt 100%[===================>] 589.80K  --.-KB/s    in 0.003s  

2021-11-07 08:29:40 (202 MB/s) - ‘questions-words.txt’ saved [603955/603955]



In [ ]:
# 先頭15行の確認
!head -15 questions-words.txt

: capital-common-countries
Athens Greece Baghdad Iraq
Athens Greece Bangkok Thailand
Athens Greece Beijing China
Athens Greece Berlin Germany
Athens Greece Bern Switzerland
Athens Greece Cairo Egypt
Athens Greece Canberra Australia
Athens Greece Hanoi Vietnam
Athens Greece Havana Cuba
Athens Greece Helsinki Finland
Athens Greece Islamabad Pakistan
Athens Greece Kabul Afghanistan
Athens Greece London England
Athens Greece Madrid Spain


In [ ]:
# 末尾15行の確認
!tail -15 questions-words.txt

write writes say says
write writes scream screams
write writes search searches
write writes see sees
write writes shuffle shuffles
write writes sing sings
write writes sit sits
write writes slow slows
write writes speak speaks
write writes swim swims
write writes talk talks
write writes think thinks
write writes vanish vanishes
write writes walk walks
write writes work works


In [ ]:
#行数確認
!wc -l questions-words.txt

19558 questions-words.txt


In [ ]:
#64

"""
一度実行済

from tqdm import tqdm #実行がかなり長いのでtqdmでバーを導入

with open('./questions-words.txt', 'r') as f1, open('./questions-words-added.txt', 'w') as f2:
  for line in tqdm(f1,total= 19558):  # f1から1行ずつ読込み、求めた単語と類似度を追加してf2に書込む (f1は19558行ある) 
    line = line.split()
    if line[0] == ':':
      category = line[1]
    else:
      word, cos = model.most_similar(positive=[line[1], line[2]], negative=[line[0]], topn=1)[0]
      f2.write(' '.join([category] + line + [word, str(cos) + '\n']))

  """

"\n一度実行済\n\nfrom tqdm import tqdm #実行がかなり長いのでtqdmでバーを導入\n\nwith open('./questions-words.txt', 'r') as f1, open('./questions-words-added.txt', 'w') as f2:\n  for line in tqdm(f1,total= 19558):  # f1から1行ずつ読込み、求めた単語と類似度を追加してf2に書込む (f1は19558行ある) \n    line = line.split()\n    if line[0] == ':':\n      category = line[1]\n    else:\n      word, cos = model.most_similar(positive=[line[1], line[2]], negative=[line[0]], topn=1)[0]\n      f2.write(' '.join([category] + line + [word, str(cos) + '\n']))\n\n  "

In [ ]:
"""
実行済


#64を再び実行しなくてよいようにtxtファイルを保存し、ドライブにおいておく
from google.colab import files
files.download('./questions-words-added.txt')

"""

"\n実行済\n\n\n#64を再び実行しなくてよいようにtxtファイルを保存し、ドライブにおいておく\nfrom google.colab import files\nfiles.download('./questions-words-added.txt')\n\n"

In [ ]:
#Google ドライブを Google Colab にマウントする
from google.colab import drive
drive.mount('/content/drive')
%cd "/content/drive/My Drive/言語処理100本ノック/"

Mounted at /content/drive
/content/drive/My Drive/言語処理100本ノック


In [ ]:
!head -15 questions-words-added.txt

capital-common-countries Athens Greece Baghdad Iraq Iraqi 0.6351870894432068
capital-common-countries Athens Greece Bangkok Thailand Thailand 0.7137669324874878
capital-common-countries Athens Greece Beijing China China 0.7235777974128723
capital-common-countries Athens Greece Berlin Germany Germany 0.6734622120857239
capital-common-countries Athens Greece Bern Switzerland Switzerland 0.4919748306274414
capital-common-countries Athens Greece Cairo Egypt Egypt 0.7527809739112854
capital-common-countries Athens Greece Canberra Australia Australia 0.583732545375824
capital-common-countries Athens Greece Hanoi Vietnam Viet_Nam 0.6276341676712036
capital-common-countries Athens Greece Havana Cuba Cuba 0.6460992097854614
capital-common-countries Athens Greece Helsinki Finland Finland 0.6899983882904053
capital-common-countries Athens Greece Islamabad Pakistan Pakistan 0.7233326435089111
capital-common-countries Athens Greece Kabul Afghanistan Afghan 0.6160915493965149
capital-common-countrie

In [ ]:
!tail -15 questions-words-added.txt

gram9-plural-verbs write writes say says says 0.5294798612594604
gram9-plural-verbs write writes scream screams screams 0.6108009219169617
gram9-plural-verbs write writes search searches searches 0.576766312122345
gram9-plural-verbs write writes see sees sees 0.5766521692276001
gram9-plural-verbs write writes shuffle shuffles shuffles 0.5709859132766724
gram9-plural-verbs write writes sing sings sings 0.7207170724868774
gram9-plural-verbs write writes sit sits sits 0.5543497204780579
gram9-plural-verbs write writes slow slows slows 0.5092940926551819
gram9-plural-verbs write writes speak speaks speaks 0.654321551322937
gram9-plural-verbs write writes swim swims swims 0.6643378138542175
gram9-plural-verbs write writes talk talks talked 0.5447186231613159
gram9-plural-verbs write writes think thinks thinks 0.6177733540534973
gram9-plural-verbs write writes vanish vanishes disappear 0.6002706289291382
gram9-plural-verbs write writes walk walks walks 0.5534339547157288
gram9-plural-verbs w

In [ ]:
#カテゴリ名を一覧表示
import pandas as pd
lists =[]
for line in open('./questions-words.txt', mode='r'):
  line = line.split()
  if line[0].startswith(':'):
    lists.append(line[1])
pd.DataFrame(lists,columns=['カテゴリ'])

カテゴリ
0      capital-common-countries
1                 capital-world
2                      currency
3                 city-in-state
4                        family
5     gram1-adjective-to-adverb
6                gram2-opposite
7             gram3-comparative
8             gram4-superlative
9      gram5-present-participle
10  gram6-nationality-adjective
11             gram7-past-tense
12                 gram8-plural
13           gram9-plural-verbs

カテゴリ名がgramから始まるのが文法的アナロジー、その他が意味的アナロジーである。


In [ ]:
#65
with open('./questions-words-added.txt', 'r') as f:
  sem_count = 0
  sem_cor = 0
  syn_count = 0
  syn_cor = 0
  for line in f:
    line = line.split()
    if not line[0].startswith('gram'):
      sem_count += 1
      if line[4] == line[5]:
        sem_cor += 1
    else:
      syn_count += 1
      if line[4] == line[5]:
        syn_cor += 1

print(f'意味的アナロジー正解率: {sem_cor/sem_count:.4f}')
print(f'文法的アナロジー正解率: {syn_cor/syn_count:.4f}') 

意味的アナロジー正解率: 0.7309
文法的アナロジー正解率: 0.7400


In [ ]:
#66
"""
実行済(ドライブに保存済み)

!wget http://www.gabrilovich.com/resources/data/wordsim353/wordsim353.zip
!unzip wordsim353.zip
"""

'\n実行済(ドライブに保存済み)\n\n!wget http://www.gabrilovich.com/resources/data/wordsim353/wordsim353.zip\n!unzip wordsim353.zip\n'

In [ ]:
!head -15 './combined.csv'

Word 1,Word 2,Human (mean)
love,sex,6.77
tiger,cat,7.35
tiger,tiger,10.00
book,paper,7.46
computer,keyboard,7.62
computer,internet,7.58
plane,car,5.77
train,car,6.31
telephone,communication,7.50
television,radio,6.77
media,radio,7.42
drug,abuse,6.85
bread,butter,6.19
cucumber,potato,5.92


In [ ]:
!tail -15 './combined.csv'

chance,credibility,3.88
exhibit,memorabilia,5.31
concert,virtuoso,6.81
rock,jazz,7.59
museum,theater,7.19
observation,architecture,4.38
space,world,6.53
preservation,world,6.19
admission,ticket,7.69
shower,thunderstorm,6.31
shower,flood,6.03
weather,forecast,8.34
disaster,area,6.25
governor,office,6.34
architecture,century,3.78


In [ ]:
sim = []
with open('./combined.csv', 'r') as f:
  next(f)
  for line in f:  # 1行ずつ読込み、単語ベクトル、類似度を計算
    line = [s.strip() for s in line.split(',')]
    line.append(model.similarity(line[0], line[1]))
    sim.append(line)

# 確認
for i in range(10):
  print(sim[i])

print(sim)

['love', 'sex', '6.77', 0.2639377]
['tiger', 'cat', '7.35', 0.5172962]
['tiger', 'tiger', '10.00', 0.99999994]
['book', 'paper', '7.46', 0.3634626]
['computer', 'keyboard', '7.62', 0.39639163]
['computer', 'internet', '7.58', 0.40686232]
['plane', 'car', '5.77', 0.3779698]
['train', 'car', '6.31', 0.3402561]
['telephone', 'communication', '7.50', 0.33218452]
['television', 'radio', '6.77', 0.6114971]
[['love', 'sex', '6.77', 0.2639377], ['tiger', 'cat', '7.35', 0.5172962], ['tiger', 'tiger', '10.00', 0.99999994], ['book', 'paper', '7.46', 0.3634626], ['computer', 'keyboard', '7.62', 0.39639163], ['computer', 'internet', '7.58', 0.40686232], ['plane', 'car', '5.77', 0.3779698], ['train', 'car', '6.31', 0.3402561], ['telephone', 'communication', '7.50', 0.33218452], ['television', 'radio', '6.77', 0.6114971], ['media', 'radio', '7.42', 0.3899161], ['drug', 'abuse', '6.85', 0.24085768], ['bread', 'butter', '6.19', 0.6417261], ['cucumber', 'potato', '5.92', 0.5678562], ['doctor', 'nurse', 

In [ ]:
import numpy as np
from scipy.stats import spearmanr #https://qiita.com/dacciinfo/items/88debe69f9f4e927aafc スピアマン相関係数について

# スピアマン相関係数の計算
human = np.array(sim).T[2] #2列目を抜き出したいとき,転置行列の2行目とも考えられる
w2v = np.array(sim).T[3]
correlation, pvalue = spearmanr(human, w2v)

print(f'スピアマン相関係数: {correlation:.4f}')

スピアマン相関係数: 0.6850


In [ ]:
#67
#国名データが存在しないので外部から持ってくる
# https://www.kaggle.com/fernandol/countries-of-the-world/version/1 をダウンロードし、ドライブに配置

import numpy as np
import csv

with open('./countries of the world.csv') as f:
    reader = csv.reader(f)
    l = [row for row in reader]

countries = np.array(l).T[0] 
countries = list(countries)
del(countries[0]) #最初のデータは目次項目なので削除
print(countries)

#末尾に空白が含まれるので削除する&国名内の空白を_に置換する
for i in range(len(countries)):
  countries[i] = countries[i].strip()
  countries[i] = countries[i].replace(' ', '_')

print(countries)

# 単語ベクトルの取得
#modelに存在しない国(例:American_Samoa)もあったため,存在した国をベクトル化する.
countries_vec = [model[country] for country in countries if country in model]
print("実在する国数:",len(countries))
print("modelに存在した国数:",len(countries_vec),"\n")

#https://pythondatascience.plavox.info/scikit-learn/%E3%82%AF%E3%83%A9%E3%82%B9%E3%82%BF%E5%88%86%E6%9E%90-k-means k=meansについて

from sklearn.cluster import KMeans
# k-meansクラスタリング
kmeans = KMeans(n_clusters=5)
kmeans.fit(countries_vec)
for i in range(5):
    cluster = np.where(kmeans.labels_ == i)[0] #np.where https://note.nkmk.me/python-numpy-where/
    print('cluster', i)
    print(', '.join([countries[k] for k in cluster]))

['Afghanistan ', 'Albania ', 'Algeria ', 'American Samoa ', 'Andorra ', 'Angola ', 'Anguilla ', 'Antigua & Barbuda ', 'Argentina ', 'Armenia ', 'Aruba ', 'Australia ', 'Austria ', 'Azerbaijan ', 'Bahamas, The ', 'Bahrain ', 'Bangladesh ', 'Barbados ', 'Belarus ', 'Belgium ', 'Belize ', 'Benin ', 'Bermuda ', 'Bhutan ', 'Bolivia ', 'Bosnia & Herzegovina ', 'Botswana ', 'Brazil ', 'British Virgin Is. ', 'Brunei ', 'Bulgaria ', 'Burkina Faso ', 'Burma ', 'Burundi ', 'Cambodia ', 'Cameroon ', 'Canada ', 'Cape Verde ', 'Cayman Islands ', 'Central African Rep. ', 'Chad ', 'Chile ', 'China ', 'Colombia ', 'Comoros ', 'Congo, Dem. Rep. ', 'Congo, Repub. of the ', 'Cook Islands ', 'Costa Rica ', "Cote d'Ivoire ", 'Croatia ', 'Cuba ', 'Cyprus ', 'Czech Republic ', 'Denmark ', 'Djibouti ', 'Dominica ', 'Dominican Republic ', 'East Timor ', 'Ecuador ', 'Egypt ', 'El Salvador ', 'Equatorial Guinea ', 'Eritrea ', 'Estonia ', 'Ethiopia ', 'Faroe Islands ', 'Fiji ', 'Finland ', 'France ', 'French Guian

In [ ]:
#68
from matplotlib import pyplot as plt
from scipy.cluster.hierarchy import dendrogram, linkage

plt.figure(figsize=(25, 8),dpi=720) #細かいのでdpiを上げて見えやすくする
Z = linkage(countries_vec, method='ward')
dendrogram(Z, labels=countries)
plt.show()

In [ ]:
#69
!pip install bhtsne

     |████████████████████████████████| 86 kB 4.5 MB/s 
  Created wheel for bhtsne: filename=bhtsne-0.1.9-cp37-cp37m-linux_x86_64.whl size=214594 sha256=08296608389e7f5ce652879a6df07ce91ad2aa9c4dfe857324ecf99d57f16ca1
  Stored in directory: /root/.cache/pip/wheels/e4/4c/71/26b7b0736d179d6bfe9d753629955515bf7ba7c1c8a8d98cb4
Successfully built bhtsne


In [ ]:
import bhtsne

embedded = bhtsne.tsne(np.array(countries_vec).astype(np.float64), dimensions=2, rand_seed=42)
plt.figure(figsize=(25, 25),dpi=720)
plt.scatter(np.array(embedded).T[0], np.array(embedded).T[1])
for (x, y), name in zip(embedded, countries):
    plt.annotate(name, (x, y))
plt.show()